# Imports

In [62]:
import requests
from bs4 import BeautifulSoup
import numpy as np
import sys
import copy
import re
import csv
import os
from neo4j import GraphDatabase
from neo4j.exceptions import CypherSyntaxError
from SPARQLWrapper import SPARQLWrapper, JSON  # pip install sparqlwrapper

# Defined functions

In [63]:
def split_csv(filehandler, delimiter=',', row_limit=10_000, output_name_template='output_%s.csv', output_path='.', keep_headers=True):
    """
    Splits CSV file into multiple pieces.
    
    Arguments:
        `row_limit`: The number of rows you want in each output file. 10_000 by default.
        `output_name_template`: A %s-style template for the numbered output files.
        `output_path`: Where to put the output files.
        `keep_headers`: Whether or not to print the headers in each output file.
    Example usage:
        >> split_csv(open(r"C:\example\somefile.csv", "r"), output_name_template="wdLabels_%s.csv", output_path=r"C:\example\catalog")
    """
    import csv
    reader = csv.reader(filehandler, delimiter=delimiter)
    current_piece = 1
    current_out_path = os.path.join(
        output_path,
        output_name_template % current_piece
    )
    current_out_writer = csv.writer(open(current_out_path, 'w', newline=''), delimiter=delimiter)
    current_limit = row_limit
    if keep_headers:
        headers = next(reader)
        current_out_writer.writerow(headers)
    for i, row in enumerate(reader):
        if i + 1 > current_limit:
            current_piece += 1
            current_limit = row_limit * current_piece
            current_out_path = os.path.join(
                output_path,
                output_name_template % current_piece
            )
            current_out_writer = csv.writer(open(current_out_path, 'w', newline=''), delimiter=delimiter)
            if keep_headers:
                current_out_writer.writerow(headers)
        current_out_writer.writerow(row)

In [64]:
def get_sparql_results(endpoint_url, query):
    # Helper function
    user_agent = f"WDQS-example Python/{sys.version_info[0]}.{sys.version_info[1]}"  # https://w.wiki/CX6
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    return sparql.query().convert()

In [68]:
def preprocess_input_list(input_list):
    # Helper function
    augmented = copy.deepcopy(input_list)
    for name in input_list:
        name_without_parentheses = re.sub(r"\([^()]*\)", "", name)
        if name != name_without_parentheses:
            augmented.append(name_without_parentheses)
    return augmented

In [69]:
def scrape_qcodes(list, humans_only=False, first_only=False):
    """
    Gets Q codes and urls for wikidata pages from the first page of search results.
    
    list: list of search names, eg. ['Fryderyk Chopin', 'Ferenc Liszt', 'Wojciech Żywny']
    first_only: if True, gets data from the first link (result) only
    returns: list of dicts (search_name, page_name, description, Qcode, wiki_url)
             if page with given name doesn't exist, its qcode is ommited
    """
    list = preprocess_input_list(list)
    retv = []
    input_length = len(list)
    for i, search_name in enumerate(list):
        print(f"Scraping... {i+1}/{input_length} ... " + search_name)
        url = f"https://www.wikidata.org/w/index.php?go=Go&search={search_name}"
        r = requests.get(url)
        soup = BeautifulSoup(r.text, "html.parser")
        for item in soup.find_all('li', class_="mw-search-result mw-search-result-ns-0"):
            page_name = item.find('a', title=True)['title'].lstrip('\u200e').split('\u200e')[0]
            try:
                description = item.find('a', title=True)['title'].lstrip('\u200e').split('\u200e')[2]
            except IndexError:
                description = None
            href = item.find('a', href=True).get('href')
            Qcode = href.lstrip('/wiki/')
            wiki_url = f"https://www.wikidata.org{href}"
            if humans_only:
                human_test = get_all_human_objects([Qcode])
                if human_test:
                    if Qcode not in [d['Qcode'] for d in retv]:
                        retv.append({'search_name': search_name, 'page_name': page_name, 'description':description, 'Qcode': Qcode, 'wiki_url': wiki_url,})
                    if first_only:
                        break
            else:
                if Qcode not in [d['Qcode'] for d in retv]:
                    retv.append({'search_name': search_name, 'page_name': page_name, 'description':description, 'Qcode': Qcode, 'wiki_url': wiki_url,})
                if first_only:
                    break
    return retv

In [70]:
def get_all_triples_and_qcodes(Qcode, allow_literals=True):
    """
    Args:
        Qcode: wikidata subject Qcode, eg.: 'Q255'
        allow_literals: whether to allow returning literal objects (objects not represented as wikidata/wikimedia pages) associated with subject's Qcode

    Returns (First value returned): 
        list of tuples representig RDF triples (object-predicate-subject) and labels associated with each wikidata entity

        Example tuple representing RDF triple:
            ('http://www.wikidata.org/entity/Q255',
            'http://www.wikidata.org/entity/P19',
            'http://www.wikidata.org/entity/Q586',
            'Ludwig van Beethoven',
            'place of birth',
            'Bonn')
        Tuple contents:
            (object,
            predicate,
            subject,
            objectLabel,
            predicateLabel,
            subjectLabel)

    Returns (Second value returned): 
        list of all Qcodes of wikidata objects associated with provided subject (Qcode)

        Example:
            ['Q255', Q'1268']
    """
    #  UWAGA:  Z jakiegoś powodu query poniżej zwraca wielokrotnie zduplikowane wyniki, pewnie błąd leży po stronie twórców biblioteki SPARQLWrapper.
    #          To samo zapytanie wprwadzowne w https://query.wikidata.org/ zwraca normalne, nie powielane wyniki.
    #          Poprawiłem to dopiero przy dodawaniu krotek do listy trójek RDF.
    

    if isinstance(Qcode, list):
        list_of_wdqcodes = ["wd:" + qcode for qcode in Qcode]
        query = """SELECT DISTINCT ?s ?sLabel ?wd ?wdLabel ?o ?oLabel   WHERE {{
        SERVICE wikibase:label {{ bd:serviceParam wikibase:language "en,pl". }}
        VALUES ?s {{ {} }}
        ?s ?wdt ?o.
        ?wd wikibase:directClaim ?wdt.
        ?wd rdfs:label ?wdLabel.
        FILTER((LANG(?wdLabel)) = "en")
        }}
        ORDER BY (xsd:integer(STRAFTER(STR(?wd), "http://www.wikidata.org/entity/P")))""".format(' '.join(list_of_wdqcodes))
    else:
        query = """SELECT DISTINCT ?s ?sLabel ?wd ?wdLabel ?o ?oLabel   WHERE {
        SERVICE wikibase:label { bd:serviceParam wikibase:language "en,pl". }
        VALUES ?s { wd:%s }
        ?s ?wdt ?o.
        ?wd wikibase:directClaim ?wdt.
        ?wd rdfs:label ?wdLabel.
        FILTER((LANG(?wdLabel)) = "en")
        }
        ORDER BY (xsd:integer(STRAFTER(STR(?wd), "http://www.wikidata.org/entity/P")))"""%(Qcode)
    # print(query) 
    endpoint_url = "https://query.wikidata.org/sparql"
    results = get_sparql_results(endpoint_url, query)

    # list_of_wdqcodes = ["wd:" + qcode for qcode in list_of_qcodes]
    # query_check_objects = """SELECT ?qcode ?qcodeLabel WHERE {{
    # SERVICE wikibase:label {{ bd:serviceParam wikibase:language "en,pl". }}
    # VALUES ?qcode {{ {} }}
    # ?qcode wdt:P31 wd:Q5.
    # }}""".format(' '.join(list_of_wdqcodes))

    list_of_triples = []
    for result in results["results"]["bindings"]:
        # print(result['wdLabel']['value'])
        try:
            if result['wdLabel']['value'].__contains__('date'):  # np. Personendatenbank Germania Sacra tu wchodzi, ale to nie data...
                if "http://www.wikidata.org/.well-known" in result['oLabel']['value']:  # http://www.wikidata.org/.well-known/genid/c9a8b2f22783c60e6bf383200d9285f7 czasem są randomowe cosie w miejsach na daty
                    # t = (result['s']['value'], result['wd']['value'], result['o']['datatype'], result['sLabel']['value'], result['wdLabel']['value'], "NoData")
                    # stop = True
                    continue
                else:
                    t = (result['s']['value'], result['wd']['value'], result['o']['datatype'], result['sLabel']['value'], result['wdLabel']['value'], result['oLabel']['value'])
        except KeyError: # Personendatenbank Germania Sacra... 
            pass  # Personendatenbank Germania Sacra... 
        if not allow_literals:
            if result['o']['type'] != 'literal':
                t = (result['s']['value'], result['wd']['value'], result['o']['value'], result['sLabel']['value'], result['wdLabel']['value'], result['oLabel']['value'])
        else:
            t = (result['s']['value'], result['wd']['value'], result['o']['value'], result['sLabel']['value'], result['wdLabel']['value'], result['oLabel']['value'])
        if t not in list_of_triples:
            list_of_triples.append(t)

        # ^ WTF, ten kod wyżej nie ma sensu, nie wiem co myślałem jak to pisałem i ... czemu to działa to z datami? Jeśli result['wdLabel']['value'].__contains__('date') i allow_literals=True, czemu nie daje to błędów? 

    object_qcodes = []
    for t in list_of_triples:
        object_url = t[2]
        if "http://www.wikidata.org/entity/Q" in object_url:
            Qcode = object_url[object_url.rfind('Q'):]
            object_qcodes.append(Qcode)

    return list_of_triples, object_qcodes

In [71]:
def get_all_human_objects(list_of_qcodes):
    """
    Filters wikidata objects based on provided Qcodes. Returns only objects which are instance_of human.

    Args:
        list_of_qcodes example: ['Q255', Q'1268']
    
    Returns:
        list of tuples representing humans (qcode, wikidata object url, name)
    """
    #  UWAGA:  Z jakiegoś powodu query poniżej zwraca wielokrotnie zduplikowane wyniki, pewnie błąd leży po stronie twórców biblioteki SPARQLWrapper.
    #          To samo zapytanie wprwadzowne w https://query.wikidata.org/ zwraca normalne, nie powielane wyniki.
    #          Poprawiłem to przy przygotowywaniu zwracanego wyniku
    list_of_wdqcodes = ["wd:" + qcode for qcode in list_of_qcodes]
    query_check_objects = """SELECT ?qcode ?qcodeLabel WHERE {{
    SERVICE wikibase:label {{ bd:serviceParam wikibase:language "en,pl". }}
    VALUES ?qcode {{ {} }}
    ?qcode wdt:P31 wd:Q5.
    }}""".format(' '.join(list_of_wdqcodes))
    endpoint_url="https://query.wikidata.org/sparql"
    humans = get_sparql_results(endpoint_url, query_check_objects)
    urls_qcodes_names = []
    for r in humans["results"]["bindings"]:
        url_qcode_and_name = (r['qcode']['value'][r['qcode']['value'].rfind('Q'):], r['qcode']['value'], r['qcodeLabel']['value'])
        if url_qcode_and_name not in urls_qcodes_names:
            urls_qcodes_names.append(url_qcode_and_name)
    return urls_qcodes_names
    

In [73]:
rdf_dict = dict()
ALL_VISITED_QCODES_WITH_GATHERED_RDF_INFO = []
def recursive_get_rdf_info(input_qcodes, level=3):
    """For each provided qcode gets all rdf triples from wikidata. Also gets all rdf triples for humans associated with provided qcodes.
    If level=2, then also gets all rdf triples for humans associated with humans associated provided qcodes, etc...

    Args:
        input_qcodes (List): list of qcodes
        level (int, optional): "Depth of the recursive tree". Defaults to 3.

    Returns:
        Dict: Dictionary with qcodsccanocfdsgjwkdbfj:)lk]dsgdsa TODO ogarnąć docstringa i funkcję(przyspieszyć/napisać innym sposobem) 
    """
    print("Doing: ", input_qcodes)
    global rdf_dict
    global ALL_VISITED_QCODES_WITH_GATHERED_RDF_INFO
    current_humans = []
    length = len(input_qcodes)

    for i, Q in enumerate(input_qcodes):
        if Q in ALL_VISITED_QCODES:
            continue
        triples, all_qcodes = get_all_triples_and_qcodes(Q, allow_literals=True)
        rdf_dict[Q] = triples
        ALL_VISITED_QCODES_WITH_GATHERED_RDF_INFO.append(Q)
        tuples = get_all_human_objects(all_qcodes)
        humans = [t[0] for t in tuples]  # human qcodes associated with Q qcode

        for new_qcode in humans:
            if new_qcode not in current_humans and new_qcode not in ALL_VISITED_QCODES_WITH_GATHERED_RDF_INFO:
                current_humans.append(new_qcode)

        # for new_qcode in humans:
        #     if new_qcode not in current_humans:
        #         current_humans.append(new_qcode)
        #     triples, all_qcodes = get_all_triples_and_qcodes(new_qcode, allow_literals=True)  # czy to jest tu potrzebne??? moze w kolejnym kroku zrobimy get all triples and qcodes tam wyzej, gdy ten qcode czlowiek bedzie w inpucie funkcji.   ... ALL_VISITED_QCODES
        #     rdf_dict[new_qcode] = triples

        #     if Q in ALL_VISITED_QCODES_WITH_GATHERED_RDF_INFO:
        #         continue

        print(f"Level {level} {i+1}/{length}")
    if level > 0:
        print("Done: ", input_qcodes)
        return recursive_get_rdf_info(current_humans, level=level-1)
    else:  # level == 0
        print("Done: ", input_qcodes)
        return rdf_dict

In [74]:
ALL_LIST = list()
ALL_DICT = dict()
def return_humans(input_humans, stop_level=4):
    global ALL_DICT
    global ALL_LIST
    if stop_level==0:
        print("reached stop level, not doing ", input_humans)
        return ALL_DICT
    print(f"doing {stop_level}", input_humans)
    humans_new_input = []
    for Q in input_humans:
        if Q not in ALL_LIST:
            triples, qcodes = get_all_triples_and_qcodes(Q, allow_literals=True)
            ALL_DICT[Q] = triples
            ALL_LIST.append(Q)
            humans_new_input += [t[0] for t in get_all_human_objects(qcodes)]
    print("ALL_LIST len = ", len(ALL_LIST))
    return return_humans(humans_new_input, stop_level=stop_level-1)
    

# Input: List of persons ```(names from .txt file)```

In [76]:
with open("unique_persons.txt", 'r') as f:
    input = [name for name in f.read().splitlines() if len(name.split())!=1]  # odrzucam osoby określone pojedynczym wyrazem, np. 'Fryderyk'
    
input = ['Beethoven', 'Rachmaninoff', 'Mahler', 'Delta rzeki Okawango', 'Susanne Gibson-Milne', 'asfa fafasfs', 'sekwoja', 'Pierre']

In [77]:
print(len(input))
input

8


['Beethoven',
 'Rachmaninoff',
 'Mahler',
 'Delta rzeki Okawango',
 'Susanne Gibson-Milne',
 'asfa fafasfs',
 'sekwoja',
 'Pierre']

# Q-codes for names from input_list ```(Q-codes from wikidata search page)```

In [78]:
original_persons = scrape_qcodes(list=input, humans_only=True, first_only=True)  # 8m 30s dla 399 osób z listów z pliu .txt

Scraping... 1/8 ... Beethoven
Scraping... 2/8 ... Rachmaninoff
Scraping... 3/8 ... Mahler
Scraping... 4/8 ... Delta rzeki Okawango
Scraping... 5/8 ... Susanne Gibson-Milne
Scraping... 6/8 ... asfa fafasfs
Scraping... 7/8 ... sekwoja
Scraping... 8/8 ... Pierre


In [79]:
original_persons.sort(key=lambda d: d['search_name'])
print(len(original_persons))
original_persons

5


[{'search_name': 'Beethoven',
  'page_name': 'Ludwig van Beethoven',
  'description': 'German composer (1770–1827)',
  'Qcode': 'Q255',
  'wiki_url': 'https://www.wikidata.org/wiki/Q255'},
 {'search_name': 'Mahler',
  'page_name': 'Gustav Mahler',
  'description': 'Austrian late-Romantic composer',
  'Qcode': 'Q7304',
  'wiki_url': 'https://www.wikidata.org/wiki/Q7304'},
 {'search_name': 'Pierre',
  'page_name': 'Jean Baptiste Louis Pierre',
  'description': 'French botanist (1833-1905)',
  'Qcode': 'Q2593213',
  'wiki_url': 'https://www.wikidata.org/wiki/Q2593213'},
 {'search_name': 'Rachmaninoff',
  'page_name': 'Sergei Rachmaninoff',
  'description': 'Russian composer, pianist, and conductor (1873–1943)',
  'Qcode': 'Q131861',
  'wiki_url': 'https://www.wikidata.org/wiki/Q131861'},
 {'search_name': 'sekwoja',
  'page_name': 'Sequoyah',
  'description': 'Cherokee silversmith and creator of the Cherokee syllabary',
  'Qcode': 'Q313595',
  'wiki_url': 'https://www.wikidata.org/wiki/Q31

In [82]:
input_qcodes = [d['Qcode'] for d in original_persons]
input_qcodes

['Q255', 'Q7304', 'Q2593213', 'Q131861', 'Q313595']

In [83]:
input_persons_wo_qcode = set(input) - {d['search_name'] for d in original_persons}
# with open ("input_persons_wo_qcode.txt", "w") as f:
#     f.write(str(input_persons_wo_qcode))
print(len(input_persons_wo_qcode))
input_persons_wo_qcode

3


{'Delta rzeki Okawango', 'Susanne Gibson-Milne', 'asfa fafasfs'}

In [84]:
extra_persons_w_qcode = {d['search_name'] for d in original_persons} - set(input)
# with open ("extra_persons_w_qcode.txt", "w") as f:
#     f.write(str(extra_persons_w_qcode))
print(len(extra_persons_w_qcode))
extra_persons_w_qcode

0


set()

# Humans associated with names from original_list ```(N levels of depth...)```

In [39]:
# SLOW... prszyspeszyć działanie funkcji TODO

# rdf_info = recursive_get_rdf_info(input_qcodes, level=5)
rdf_info = return_humans(input_qcodes, stop_level=3)

doing 3 ['Q255', 'Q7304', 'Q2593213', 'Q131861', 'Q313595']
ALL_LIST len =  5
doing 2 ['Q254', 'Q1339', 'Q7349', 'Q51088', 'Q93373', 'Q193673', 'Q213556', 'Q213558', 'Q215333', 'Q311378', 'Q314164', 'Q472851', 'Q570845', 'Q685156', 'Q693052', 'Q1246313', 'Q1948037', 'Q2153541', 'Q6374627', 'Q10336787', 'Q14507972', 'Q15823075', 'Q16191592', 'Q63255363', 'Q79028', 'Q156898', 'Q215588', 'Q18543341', 'Q108145344', 'Q112641849', 'Q313970', 'Q335006', 'Q366536', 'Q553959', 'Q18013388', 'Q75318115', 'Q108840546', 'Q108840547', 'Q6969632']
ALL_LIST len =  44
doing 1 ['Q1339', 'Q7349', 'Q76555', 'Q84464', 'Q106641', 'Q151953', 'Q156023', 'Q156280', 'Q157928', 'Q167981', 'Q283651', 'Q310518', 'Q311378', 'Q452098', 'Q550279', 'Q615681', 'Q697804', 'Q729164', 'Q2422110', 'Q1340', 'Q48345', 'Q57212', 'Q57225', 'Q57487', 'Q60965', 'Q61689', 'Q61972', 'Q66671', 'Q67366', 'Q68255', 'Q76428', 'Q76485', 'Q106641', 'Q107277', 'Q153637', 'Q215995', 'Q309470', 'Q425612', 'Q445696', 'Q470198', 'Q508635', '

In [86]:
print(f"{len(rdf_info.keys())=}")
rdf_info

len(rdf_info.keys())=262


{'Q255': [('http://www.wikidata.org/entity/Q255',
   'http://www.wikidata.org/entity/P18',
   'http://commons.wikimedia.org/wiki/Special:FilePath/Beethoven.jpg',
   'Ludwig van Beethoven',
   'image',
   'http://commons.wikimedia.org/wiki/Special:FilePath/Beethoven.jpg'),
  ('http://www.wikidata.org/entity/Q255',
   'http://www.wikidata.org/entity/P18',
   'http://commons.wikimedia.org/wiki/Special:FilePath/Beethoven%203.jpg',
   'Ludwig van Beethoven',
   'image',
   'http://commons.wikimedia.org/wiki/Special:FilePath/Beethoven%203.jpg'),
  ('http://www.wikidata.org/entity/Q255',
   'http://www.wikidata.org/entity/P19',
   'http://www.wikidata.org/entity/Q586',
   'Ludwig van Beethoven',
   'place of birth',
   'Bonn'),
  ('http://www.wikidata.org/entity/Q255',
   'http://www.wikidata.org/entity/P20',
   'http://www.wikidata.org/entity/Q1741',
   'Ludwig van Beethoven',
   'place of death',
   'Vienna'),
  ('http://www.wikidata.org/entity/Q255',
   'http://www.wikidata.org/entity/P21'

In [89]:
# # Zapisanie rdf_info w formacie json
# import json
# with open("rdf_info_25_04_lvl3_stoplevel4_persons14100.json", "w") as f:
#     json.dump(rdf_info, f)  # no idntent arg if you want smaller filesize

In [90]:
# # Ładowanie już zapisanego rdf_info (dla 399 osób z listy? chyba tak, nie jestem pewien - lepiej jeszcze raz wygenerować ten plik)
# import json
# rdf_info = json.load(open(r'C:\GraphProject\Places_People_and_Events\Krzysztof\rdf_info_25_04_lvl3_stoplevel4_persons14100.json'))
# len(rdf_info)

In [91]:
qcodes_to_check = set()
for Q in rdf_info.keys():
    qcodes_to_check.add(Q)
    for rdf_tuple in rdf_info[Q]:
        if rdf_tuple[4] == "FactGrid item ID":
            continue
        object_url = rdf_tuple[2]
        qcode = object_url[object_url.rfind('Q'):]
        if len(qcode) > 1:
            if qcode[1:].isdigit():
                qcodes_to_check.add(qcode)
                if (qcode=='Q383232'):
                    print(Q, rdf_info[Q])
print(f"{len(qcodes_to_check) = }")

qcodes_to_check_split = []
n_size = 500  # splitting qcodes_to_check into lists of n_size (500) elements, because URI cannot be too large in function get_all_human_objects()
length = len(qcodes_to_check)
temp = []
for i, qcode in enumerate(qcodes_to_check):
    temp.append(qcode)
    if i%n_size == n_size-1:
        qcodes_to_check_split.append(temp)
        temp = []
    if i == length-1:
        if len(temp) > 0:
            qcodes_to_check_split.append(temp)
print(f"{len(qcodes_to_check_split) = }")

all_humans = []
n_lists = len(qcodes_to_check_split)
for i, lista in enumerate(qcodes_to_check_split):
    temp_list = get_all_human_objects(lista)
    all_humans += temp_list
# ^ 1m 30s dla len(qcodes_to_check) = 60829

len(qcodes_to_check) = 2605
len(qcodes_to_check_split) = 6


In [93]:
print(f"{len(all_humans) = }")
all_humans

len(all_humans) = 952


[('Q1151', 'http://www.wikidata.org/entity/Q1151', 'Hector Berlioz'),
 ('Q7314', 'http://www.wikidata.org/entity/Q7314', 'Igor Stravinsky'),
 ('Q7315', 'http://www.wikidata.org/entity/Q7315', 'Pyotr Ilyich Tchaikovsky'),
 ('Q28858', 'http://www.wikidata.org/entity/Q28858', 'Ludwig Rellstab'),
 ('Q36234', 'http://www.wikidata.org/entity/Q36234', 'Charles III of Spain'),
 ('Q41309', 'http://www.wikidata.org/entity/Q41309', 'Franz Liszt'),
 ('Q57286', 'http://www.wikidata.org/entity/Q57286', 'Fanny Mendelssohn'),
 ('Q57369', 'http://www.wikidata.org/entity/Q57369', 'Nicolaus Bruhns'),
 ('Q61972',
  'http://www.wikidata.org/entity/Q61972',
  'Johann Ernst III, Duke of Saxe-Weimar'),
 ('Q62659',
  'http://www.wikidata.org/entity/Q62659',
  'William Ernest, Duke of Saxe-Weimar'),
 ('Q66033',
  'http://www.wikidata.org/entity/Q66033',
  'Johann Bernhard Bach the younger'),
 ('Q67366',
  'http://www.wikidata.org/entity/Q67366',
  'Johann Christoph Altnickol'),
 ('Q69912', 'http://www.wikidata.

# Creating neo4j graph

## connect to database

In [94]:
driver = GraphDatabase.driver("bolt://localhost:7687", auth=("neo4j", "password"))
driver.verify_connectivity()
session = driver.session(database="wikidatadev")

## create Person nodes

In [54]:
all_humans_qcodes = []
for human in all_humans:
    qcode, wd_url, name = human
    all_humans_qcodes.append(qcode)
    try:
        cypher_query = f"""MERGE (:Person{{name: "{name}", wd_url: "{wd_url}"}})"""
        session.run(cypher_query)
    except CypherSyntaxError:  #  Karol Stanisław "Panie Kochanku" Radziwiłł (Q386484) 
        cypher_query = f"""MERGE (:Person{{name: '{name}', wd_url: '{wd_url}'}})"""
        session.run(cypher_query)
# ^ 2m16s dla len(all_humans) =~ 30_000 (powstałe z 399 osób z inputu)

In [55]:
cypher_query = f"""
CREATE INDEX person_wd_idx IF NOT EXISTS
FOR (n:Person)
ON (n.wd_url)
"""
session.run(cypher_query)

cypher_query = f"""
CREATE INDEX person_name_idx IF NOT EXISTS
FOR (n:Person)
ON (n.name)
"""
session.run(cypher_query)

# jak sprawdzić, czy indexy się założyły?

## create other nodes, edges & connect to Person nodes  WORK IN PROGRESS, VERY SLOW...

In [58]:
# SLOW
ERRORS = []
length = len(rdf_info.keys())
print("Creating edges & object nodes for: ")
for i, qcode in enumerate(rdf_info.keys()):
    print(f"{qcode} {i+1} / {length}")
    for t in rdf_info[qcode]:
        object_name, object_url = t[5].replace("'", "\\'"), t[2].replace("'", "\\'")

        object_label = "wdLabel"
        object_qcode = object_url[object_url.rfind("Q"):]
        if object_qcode in all_humans_qcodes:
            object_label = "Person"
        else:
            cypher_query = f"""MERGE (:{object_label}{{name: '{object_name}', wd_url: '{object_url}'}})"""
            try:
                session.run(cypher_query)
            except Exception as e:
                ERRORS.append(("MERGE NODE", object_url, cypher_query, e))

        cypher_illegal_edgename_chars = ["'", ",", "(", ")", "-", ".", "/", "&", "’", "+", "+d'-", ":"]
        edge_name = t[4].replace(' ', '_').replace("–", "_")
        for c in cypher_illegal_edgename_chars:
            edge_name = edge_name.replace(c, "")
        edge_name = edge_name.upper()
        edge_url = t[1]

        subject_url = t[0].replace("'", "\\'")
        person_name = t[3].replace("'", "\\'")
        try:
            s = f"""
            MATCH (p:Person), (l:{object_label}) 
            WHERE p.wd_url="{subject_url}" AND l.wd_url='{object_url}'
            MERGE (p)-[:`{edge_name}` {{wd_url: '{edge_url}', source: 'wikidata'}}]->(l)
            """
            session.run(s)
        except Exception as e:
            ERRORS.append(("MERGE EDGE", object_url, s, e))

Creating edges & object nodes for: 
Q255 1 / 262
Q7304 2 / 262
Q2593213 3 / 262
Q131861 4 / 262
Q313595 5 / 262
Q254 6 / 262
Q1339 7 / 262
Q7349 8 / 262
Q51088 9 / 262
Q93373 10 / 262
Q193673 11 / 262
Q213556 12 / 262
Q213558 13 / 262
Q215333 14 / 262
Q311378 15 / 262
Q314164 16 / 262
Q472851 17 / 262
Q570845 18 / 262
Q685156 19 / 262
Q693052 20 / 262
Q1246313 21 / 262
Q1948037 22 / 262
Q2153541 23 / 262
Q6374627 24 / 262
Q10336787 25 / 262
Q14507972 26 / 262
Q15823075 27 / 262
Q16191592 28 / 262
Q63255363 29 / 262
Q79028 30 / 262
Q156898 31 / 262
Q215588 32 / 262
Q18543341 33 / 262
Q108145344 34 / 262
Q112641849 35 / 262
Q313970 36 / 262
Q335006 37 / 262
Q366536 38 / 262
Q553959 39 / 262
Q18013388 40 / 262
Q75318115 41 / 262
Q108840546 42 / 262
Q108840547 43 / 262
Q6969632 44 / 262
Q76555 45 / 262
Q84464 46 / 262
Q106641 47 / 262
Q151953 48 / 262
Q156023 49 / 262
Q156280 50 / 262
Q157928 51 / 262
Q167981 52 / 262
Q283651 53 / 262
Q310518 54 / 262
Q452098 55 / 262
Q550279 56 / 262
Q615

In [22]:
# ^ 9s dla len(rdf_info.keys()) = 35 len(all_humans) = 88
# ^ 45s dla len(rdf_info.keys()) = 36 len(all_humans) = 170
# ^ 936m 52s dla len(rdf_info.keys()) = 13171 len(all_humans) = 29966

In [56]:
# ERRORS
# ^ lista ERRORS była pusta dla 936m 52s dla len(rdf_info.keys()) = 13171 len(all_humans) = 29966. To pewnie jakiś błąd jupytera(?), może za długo komórka działała. Jakeiś errory musiały się pojawić....

In [97]:
non_person_node_label = "wdLabel"
cypher_query = f"""
CREATE INDEX object_wd_idx IF NOT EXISTS
FOR (n:{non_person_node_label})
ON (n.wd_url)
"""
session.run(cypher_query)

cypher_query = f"""
CREATE INDEX object_name_idx IF NOT EXISTS
FOR (n:{non_person_node_label})
ON (n.name)
"""
session.run(cypher_query)

## delete all nodes

In [47]:
# # DELETE ALL
# s="""MATCH (n)
# CALL { WITH n
# DETACH DELETE n
# } IN TRANSACTIONS;"""
# session.run(s)

## session close

In [ ]:
# session.close()

# Komentarze
Zbiór niezbyt dobrze uporządkowanych myśli i nieścisłych wyrażeń *(informacje dla mnie, po jakimś czasie i tak przestałem aktualizować tę sekcję)*

Co zrobiłem:
* uporządkowałem kod
* odrzuciłem pojedyncze nazwy z listy osób, np. "Pierre"
* ```get_all_triples_and_qcodes()``` dodałem opcję zostawienia tych objects, które nie są Qcodami w wikidata (różne literały, często są to jakieś id w muzeach czy innych zbiorach danych, wcześniej to odrzuciłem bo wydało mi się nieprzydatne) 
* ^ ale wd_url będzie wtedy literałem, a nie urlem w grafie. Nie jest to chyba duży problem i może tak zostać.
* dla krawędzi: uppercase nazw i dodanie atrybutu ```source: 'wikidata' ```
* dla każdego subject z listy sprawdzenie wszystkich powiązanych objects i zapisanie qcodów tych obiektów, które są ```instance_of``` --> ```human```
* ```scrape_qcodes(list, humans_only=False, first_only=False)``` dodałem sposób na dostanie Qcode tylko pierwszego znalezionego człowieka na wikidata
* zrezygnowałem z atrybutu ```description``` dla scrapeowanych qcodów (w grafie)
* rekurencyjne pobieranie info o ludziach połączonych z ludźmi z inputu

Kilka problematycznych kwestii:
* a może nie brać osób z listów Paderewskiego, a zostawić tylko osoby z listów Chopina?
* osoba, o którą nam chodzi nie jest pierwszym wynikiem na liście wyszukiwania w wikidata
* czy kontrolujemy manualnie poprawność osób dodanych z wikidata? (chodzi o osoby z input_list)
* biblioteka SPARQLWrapper nie działa dobrze, zwraca często zmultiplikowane wyniki i spowalnia działanie programu
* osoby, które są na najniższym poziome (liście drzewa) nie mają żadnych atrybutów (trójek rdf), bo kiedyś ten łańcuch trzeba skończyć. Pytanie w jaki sposób. 
* w grafie prawdopodobnie będą błędy, np. randomowe osoby nazywające się tak samo jak np. te wspomniane w listach, a tych wspomnianych nie będzie w grafie
* będą sobie pływały randomowe węzły osób w tym grafie, np. Q383232 (Afiat Yuris Wirawan, gracz badmintona) bo np Rachmaninov ma "FactGrid item ID": Q383232
* ^ EDIT:   naprawiłem to dla tego specyficznego przypadku krawędzi "FactGrid item ID", u nich wszystkie ID są postaci takiej jak Qcody na wikidata
* ^         ale mogą się pojawić inne randomowe osoby i przez to nie będzie tworzony węzęł z obiektem o nazwie np. Q123 i nie będzie krawędzi między subjectem(osobą) a obiektem/randomową osobą

['Etienne',
 'Perrichet',
 'Pierre',
 'Alexis',
 'Grandville',
 'Rafael',
 'Voltaire']

Granville https://www.wikidata.org/wiki/Q744442 ???

Voltaire https://www.wikidata.org/wiki/Q9068 ???

Pierre służący Fryderyka Chopina ???

*** na DBMS wikidata_spqrql jest graf z poprzedniej wersji kodu, część problemów rozwiązałem i teraz ten graf jest nie aktualny. Zapisałem zaktualizowane rdf_info (25 kwietnia). Teraz można na podstawie tego stworzyć graf. Pytanie jak to zrobić żeby to nie trwało 9h.

*** Nie wygląda na to jakby wczytywanie z CSV miało byś szybsze...

--- na razie robię sobie przerwę od tego projektu, muszę zacząć robić pracę inżynierską i mam też inny projekt

-- https://query.wikidata.org/ do rozważenia jakby ktoś chciał się zająć pobieraniem innych danych (nie dotyczących osób)

# TODO



* Ctrl + f "TODO" w kodzie - things to work on first
* Zbyt długo trwa robienie grafu. Może zrobienie csv i potem wczytywanie csv do neo4j będzie szybsze niż pojedyncze robienie węzłów i krawędzi. Zrobić indeksy, zwiększyć limity pamięci w neo4j desktop, zrobić CSV do krawędzi i LOAD CSV, CALL IN TRANSACTIONS. Do zrobienia.
* Zbyt długo trwa recursive_get_rdf_info. Napisać szybszą funkcję, dającą ten sam wynik. 
* Może by tak oznaczać osoby (węzeł :Person), które nie mają atrybutów z wikidata (czyli w grafie powiązań z węzłami wdLabel) jakąś inną etykietą, lub jakimś atrybutem, np. "leaf"/"no_further_info"/"no_". Są to "osoby-liście", na których kończy się rekurencyjne pobieranie info o ludziach. ({all_humans} - {rdf_info.keys()}). A może nie trzeba i zostawić tak jak jest?
* Biblioteka SPARQLWrapper nie działa dobrze, zwraca często zmultiplikowane wyniki i spowalnia działanie programu, można spróbować użyć innej biblioteki lub samemu napisać.
* Może nie brać osób z listów Paderewskiego, a zostawić tylko osoby z listów Chopina?
* [EDIT] [nieważne, neo4j browser nie wyświetla krawędzi czasami] czemu wielu kompozytorów nie ma OCCUPATION -> composer? np. Robert Schumann... Wygląda na to, że czasamiu niektóre krawędzie się nie tworzą, zbadać przyczynę i naprawić.
* [DONE] Niektórych osób z input listy nie wyszukuje w wikdata. Jak się usunie dopiski w nawiasach, to już tak, np. dla "Józef Michał Poniatowski (książę)".
* [DONE] w np. DATE_OF_BIRTH są jakieś śmieci czasami, np. http://www.wikidata.org/.well-known/genid/c9a8b2f22783c60e6bf383200d9285f7. Pewnie można by w "create other nodes, edges & connect to Person nodes" sprawdzać wartość dla qcodów dat np date_of_birth, date_of_costam.


** TYLKO POMYSŁ: sporo czasu by trzeba poświęcić na sprawdzanie czy pierszy scrape'owany human z wikidata search to osoba której chcemy (czyli w jakiś sposób powiązana z Chopinem/osobami na grafie).


## sample cypher queries

In [491]:
# UWAGA: nie można traktować uzyskanych wyników jako prawdę odzwierdciedlającą rzeczywistość; dane są niekompletne i pewnie niektóre nawet są nieprawdziwe.

# MATCH (n) WHERE n.name =~ ".*Chopin.*" RETURN n

# match (n:Person)-[e:OCCUPATION]-(s) WHERE s.name CONTAINS "composer" return n,s

# MATCH (p:Person)-[l:residence]-(s)
# WHERE p.name=~'.*Chopin' or p.name=~'.*Liszt'
# RETURN p, s

# MATCH (p:Person)-[l:RESIDENCE]-(s)
# WHERE p.name=~'.*Chopin' or p.name=~'.*Beethoven.*'
# RETURN p, s

# MATCH (p:Person)-[l:STUDENT_OF]-(s)
# WHERE p.name=~'.*Frédéric Chopin.*' or p.name=~'.*Franz Liszt.*'
# RETURN p, s

# Match(p:Person)-[e:DATE_OF_BIRTH]-(l:wdLabel) return p, l

# match (n:Person) WHERE n.name CONTAINS "Bee" return n

# MATCH (p:Person)-[e:OCCUPATION]-(s:wdLabel) WHERE s.name =~ ".*singer.*" RETURN p,s

# MATCH w=(p:Person)-[e:INSTRUMENT]-(s:wdLabel)
# WITH s, COLLECT(w) as test
# ORDER BY SIZE(test) DESC
# RETURN s.name, SIZE(test)

# MATCH (p:Person)-[e:DATE_OF_BIRTH]-(d:wdLabel)
# WHERE datetime({year: 1770, month:7}) <= datetime(d.name) < datetime({year: 1771})
# WITH p, d
# ORDER BY d.name DESC
# RETURN p, d, p.name, d.name

# MATCH (p:Person)-[e:HANDEDNESS]-(s:wdLabel), (p)-[i:INSTRUMENT]-(s2:wdLabel)
# WHERE s.name =~ '.*left.*' 
# RETURN *  

# MATCH (p:Person)-[e:HANDEDNESS]-(s:wdLabel)
# WHERE s.name =~ '.*left.*' 
# RETURN *  

# MATCH (p:Person)-[e:DIFFERENT_FROM]-(o)
# WHERE p.name =~ '.*.*'
# RETURN p, o limit 200
